In [19]:
import mat4py
import numpy as np
import pandas as pd
import lanelet2

In [20]:
# read matlab file
data = mat4py.loadmat('/home/matyko/Downloads/forLanelets.mat')

In [21]:
lanes = []

for i in range(len(data["lanelets"])):
    path = np.array(data["lanelets"][i]["centerLine"])
    leftLane = np.array(data["lanelets"][i]["leftLine"])
    rightLane = np.array(data["lanelets"][i]["rightLine"])

    lanes.append([path,leftLane,rightLane])

In [22]:
#plot lane1 using plotly
import plotly.graph_objects as go

fig = go.Figure()
# plot with the same scale for x and y
fig.update_xaxes(scaleanchor = "y", scaleratio = 1)

for lane in lanes:
    fig.add_trace(go.Scatter(x = lane[0][:,0], y = lane[0][:,1], mode='lines', name='centerLine'))
    fig.add_trace(go.Scatter(x = lane[1][:,0], y = lane[1][:,1], mode='lines', name='leftLane'))
    fig.add_trace(go.Scatter(x = lane[2][:,0], y = lane[2][:,1], mode='lines', name='rightLane'))

fig.show()




In [39]:
import lanelet2
import lanelet2.core as l2_core
import lanelet2.io as l2_io
import lanelet2.projection as l2_proj
import lanelet2.projection
import lanelet2.traffic_rules as l2_rules
import os

left_points = []
right_points = []
center_points = []

# Create a Lanelet map and add the lanelet
lanelet_map = l2_core.LaneletMap()

for lane in lanes:

    left_points.clear()
    right_points.clear()
    center_points.clear()

    for i, points in enumerate(lane[1]):
        if i % 10 == 0:
            left_points.append(l2_core.Point3d(l2_core.getId(), points[0], points[1], 0))

    for i, points in enumerate(lane[2]):
        if i % 10 == 0:
            right_points.append(l2_core.Point3d(l2_core.getId(), points[0], points[1], 0))

    for i, points in enumerate(lane[0]):
        if i % 10 == 0:
            center_points.append(l2_core.Point3d(l2_core.getId(), points[0], points[1], 0))


    # delete the last 10 points from the left and right lane
    left_points = left_points[:-10]
    right_points = right_points[:-10]
    center_points = center_points[:-10]



    # Create LineStrings (borders of the lanelet)
    left_ls = l2_core.LineString3d(l2_core.getId(), left_points)
    right_ls = l2_core.LineString3d(l2_core.getId(), right_points)
    center_ls = l2_core.LineString3d(l2_core.getId(), center_points)



    # Create a lanelet from the left and right boundaries
    lanelet = l2_core.Lanelet(l2_core.getId(), left_ls, right_ls)

    # Set some attributes for the laneletb
    lanelet.attributes["subtype"] = "road"
    lanelet.attributes["one_way"] = "yes"

    lanelet_map.add(lanelet)

    # Add the linestrings to the map
    lanelet_map.add(left_ls)
    lanelet_map.add(right_ls)

projection = lanelet2.projection.UtmProjector(lanelet2.io.Origin(0, 0))

# Write the map to an OSM file
map_file = "lightweight_lanelet.osm"
l2_io.write(map_file, lanelet_map, projection)

print(f"Lanelet2 map has been saved to {map_file}")


Lanelet2 map has been saved to lightweight_lanelet.osm
